In [1]:
import pandas as pd
import numpy as np
import re
import json
import numpy as np
import timeit 
from datetime import datetime

In [2]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.callbacks import ModelCheckpoint

In [3]:
# Cufflinks wrapper on plotly
import cufflinks
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

from plotly.offline import iplot
cufflinks.go_offline()

# Set global theme

import plotly.figure_factory as ff

import plotly.graph_objects as go
import plotly.express as px

In [4]:
from sklearn.model_selection import train_test_split

In [5]:
#Selecting a central city point to center all graphs around - Swietokrzyska Subway 
center_coors=52.235176, 21.008393

In [6]:
df=pd.read_excel("RE_models_input.xlsx")

In [7]:
df.columns

Index(['Id', 'Area', 'Price', 'latitude', 'longitude', 'build_year',
       'building_floors_num', 'rooms_num', 'City', 'subdistrict', 'market',
       'Building_material', 'Building_ownership', 'Building_type',
       'Construction_status', 'floor_no', 'Heating', 'Windows_type',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm

In [8]:
df['rooms_num']=np.where(df['rooms_num']=="more",10,df['rooms_num'])

In [9]:
df.drop(columns=['floor_no',"City","district_old",'price_decrease_from_20k','price_decrease_per_10min'],inplace=True)

In [10]:
df.columns

Index(['Id', 'Area', 'Price', 'latitude', 'longitude', 'build_year',
       'building_floors_num', 'rooms_num', 'subdistrict', 'market',
       'Building_material', 'Building_ownership', 'Building_type',
       'Construction_status', 'Heating', 'Windows_type',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm',
       'Security_

In [11]:
df["distance_driving"]=(df.distance_driving_8AM+df.distance_return_driving_5PM)/2
df["distance_transit"]=(df.distance_transit_8AM+df.distance_return_transit_5PM)/2
df["time_driving"]=(df.time_driving_8AM+df.time_return_driving_5PM)/2
df["time_transit"]=(df.time_return_transit_5PM+df.time_transit_8AM)/2

In [12]:
df.drop(columns=['distance_transit_8AM', 'time_transit_8AM', 'distance_driving_8AM',
       'time_driving_8AM', 'distance_return_transit_5PM',
       'time_return_transit_5PM', 'distance_return_driving_5PM',
       'time_return_driving_5PM'],inplace=True)

# Data exploration

## Category composition

In [13]:
unique_features=["district","market","Building_material","Building_ownership","Building_type","Construction_status","Heating",
"Windows_type"]

In [14]:
for feature in unique_features:
    feature_list=["Id"]
    feature_list.append(feature)

    df_temp=df[feature_list].groupby(feature, as_index=False).count()
    df_temp.rename(columns={"Id":"share"},inplace=True)
    df_temp.sort_values(by="share",inplace=True, ascending=False)
    df_temp["share"]=df_temp["share"]/df.shape[0]
    df_temp["share"]=np.around(df_temp["share"],3)*100
    df_temp["colour"]=np.where(df_temp[feature]=="not_specified","missing_data","valid_data")
    
    fig = px.bar(df_temp, x=feature, y='share', color="colour",
                 color_discrete_sequence=["blue", "red"],
                 category_orders={"colour": ["valid_data", "missing_data"]},)
    print("\n Feature summary for {} - Share of category within whole sample".format(feature))
    fig.show()
    print("----------------------------------------------------------------------------------------------------------------------------\n\n\n")

    


 Feature summary for district - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for market - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Building_material - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Building_ownership - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Building_type - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Construction_status - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Heating - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Windows_type - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------





## Average unit price by feature 

In [15]:
for feature in unique_features:
    feature_list=["unit_price"]
    feature_list.append(feature)

    df_temp=df[feature_list]
    
    print("\n Unit price distribution in split by {}".format(feature))
    
    fig = fig = px.box(df_temp, y="unit_price", x=feature, points="suspectedoutliers");
    fig.update_yaxes(range=[5000, 25000])


    print("----------------------------------------------------------------------------------------------------------------------------\n\n\n")

    


 Unit price distribution in split by district


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by market


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Building_material


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Building_ownership


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Building_type


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Construction_status


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Heating


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Windows_type


----------------------------------------------------------------------------------------------------------------------------





# Transforming data for ML models

In [16]:
from sklearn.preprocessing import OneHotEncoder

In [17]:
df_cat=df[unique_features]

In [18]:
enc=OneHotEncoder()
enc.fit(df_cat)

one_hot_val=enc.fit_transform(df_cat).toarray().astype(int)
one_hot_columns=enc.get_feature_names(unique_features)

OneHotEncoder(categories='auto', drop=None, dtype=<class 'numpy.float64'>,
              handle_unknown='error', sparse=True)

In [19]:
df_one_hot=pd.DataFrame(one_hot_val, columns=one_hot_columns)

In [20]:
df_one_hot.columns

Index(['district_Bemowo', 'district_Bialoleka', 'district_Bielany',
       'district_Downtown', 'district_Mokotow', 'district_Ochota',
       'district_Praga', 'district_Southern Praga', 'district_Subburbs',
       'district_Targowek', 'district_Ursynow', 'district_Wawer',
       'district_Wilanow', 'district_Wlochy', 'district_Wola',
       'district_Zoliborz', 'market_primary', 'market_secondary',
       'Building_material_breezeblock', 'Building_material_brick',
       'Building_material_cellular_concrete', 'Building_material_concrete',
       'Building_material_concrete_plate', 'Building_material_hydroton',
       'Building_material_not_specified', 'Building_material_other',
       'Building_material_reinforced_concrete', 'Building_material_silikat',
       'Building_material_wood', 'Building_ownership_co_operative_ownership',
       'Building_ownership_co_operative_ownership_with_a_land_and_mortgage_registe',
       'Building_ownership_full_ownership', 'Building_ownership_not_spec

In [21]:
not_specified_idx=[]
for i in range(0,df_one_hot.columns.shape[0]):
    if "not_specified" in df_one_hot.columns[i]:
        not_specified_idx.append(i)
not_specified_idx=np.asarray(not_specified_idx)

Let's drop all "not_specified" columns and secondary market in Mokotow district (it will be used as baseline in models)

In [22]:
drop_collinear_cols=list(df_one_hot.columns[not_specified_idx])
drop_collinear_cols.append('district_Mokotow')
drop_collinear_cols.append('market_secondary')

In [23]:
def list_diff(list1, list2):
    out = []
    for ele in list1:
        if not ele in list2:
            out.append(ele)
    return out

In [24]:
df_one_hot.columns

Index(['district_Bemowo', 'district_Bialoleka', 'district_Bielany',
       'district_Downtown', 'district_Mokotow', 'district_Ochota',
       'district_Praga', 'district_Southern Praga', 'district_Subburbs',
       'district_Targowek', 'district_Ursynow', 'district_Wawer',
       'district_Wilanow', 'district_Wlochy', 'district_Wola',
       'district_Zoliborz', 'market_primary', 'market_secondary',
       'Building_material_breezeblock', 'Building_material_brick',
       'Building_material_cellular_concrete', 'Building_material_concrete',
       'Building_material_concrete_plate', 'Building_material_hydroton',
       'Building_material_not_specified', 'Building_material_other',
       'Building_material_reinforced_concrete', 'Building_material_silikat',
       'Building_material_wood', 'Building_ownership_co_operative_ownership',
       'Building_ownership_co_operative_ownership_with_a_land_and_mortgage_registe',
       'Building_ownership_full_ownership', 'Building_ownership_not_spec

In [25]:
df_cat_columns=list_diff(df_one_hot.columns,drop_collinear_cols)

In [26]:
df_cat=df_one_hot[df_cat_columns]

In [27]:
columns_base=list_diff(df.columns, unique_features)

In [28]:
drop_columns_base=[
    'Price','latitude','longitude','lon_mod','lat_mod','grid_price','sample_size','City','subdistrict'
                  ]

In [29]:
columns_base=list_diff(columns_base, drop_columns_base)

In [30]:
df_base=df[columns_base]

In [31]:
df_base.columns

Index(['Id', 'Area', 'build_year', 'building_floors_num', 'rooms_num',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm',
       'Security_types_anti_burglary_door', 'Security_types_closed_area',
       'Security_types_entryphone', 'Security_types_monitoring',
       'Security_types_roller_shutters', 'floor_num', 'unit_price',


## Combining data for modeling

In [32]:
ml_data=pd.concat([df_base,df_cat],axis=1)

In [33]:
ml_data.shape

(11788, 89)

In [34]:
ml_data.head()

Id   Area  build_year  building_floors_num rooms_num  \
0  60534950  80.10        2021                    8         4   
1  60534789  52.27        2021                    8         2   
2  60534636  64.63        2021                    8         3   
3  60441425  46.86        2020                   14         3   
4  60225257  57.40        2019                   11         3   

   Equipment_types_dishwasher  Equipment_types_fridge  \
0                           0                       0   
1                           0                       0   
2                           0                       0   
3                           0                       0   
4                           1                       1   

   Equipment_types_furniture  Equipment_types_oven  Equipment_types_stove  \
0                          0                     0                      0   
1                          0                     0                      0   
2                          0                     0                      0   
3                          0                     0                      0   
4                          1                     1                      1   

   ...  Construction_status_to_completion  Construction_status_to_renovation  \
0  ...                                  0                                  0   
1  ...                                  0                                  0   
2  ...                                  0                                  0   
3  ...                                  0                                  0   
4  ...                                  0                                  0   

   Heating_boiler_room  Heating_electrical  Heating_gas  Heating_other  \
0                    0                   0            0              0   
1                    0                   0            0              0   
2                    0                   0            0              0   
3                    0                   0            0              0   
4                    0                   0            0              0   

   Heating_urban  Windows_type_aluminium  Windows_type_plastic  \
0              0                       0                     0   
1              0                       0                     0   
2              0                       0                     0   
3              0                       0                     0   
4              1                       0                     1   

   Windows_type_wooden  
0                    0  
1                    0  
2                    0  
3                    0  
4                    0  

[5 rows x 89 columns]

In [35]:
ml_data.columns[:]

Index(['Id', 'Area', 'build_year', 'building_floors_num', 'rooms_num',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm',
       'Security_types_anti_burglary_door', 'Security_types_closed_area',
       'Security_types_entryphone', 'Security_types_monitoring',
       'Security_types_roller_shutters', 'floor_num', 'unit_price',


# Selecting best features

In [36]:
counts, bins = np.histogram(ml_data.unit_price, bins=range(0, 50000, 1000))
bins = bins[1:]

fig = px.bar(x=bins, y=counts, labels={'x':'Unit price', 'y':'count'})
fig.show()

In [37]:
X=ml_data.copy()
X=X.query("unit_price<=25000 and unit_price>5000")
y=X.unit_price
X.drop(columns=["unit_price","Id"],inplace=True)

In [38]:
from sklearn.feature_selection import SelectKBest, f_regression, chi2

In [39]:
bestfeatures = SelectKBest(score_func=f_regression, k="all")

In [40]:
fit = bestfeatures.fit(X,y)
dfscores = pd.DataFrame(fit.scores_)
dfcolumns = pd.DataFrame(X.columns)

In [41]:
featureScores = pd.concat([dfcolumns,dfscores],axis=1)
featureScores.columns = ['Specs','Score']

In [42]:
featureScores.nlargest(30,'Score')

Specs        Score
35                   distance_driving  6889.140723
36                   distance_transit  6725.884253
38                       time_transit  5360.201112
37                       time_driving  4741.988679
42                  district_Downtown  3516.937318
40                 district_Bialoleka  1766.097573
75             Building_type_tenement   769.001425
54                     market_primary   701.343385
70                Building_type_block   629.435651
46                  district_Subburbs   582.320969
1                          build_year   515.887396
86                Windows_type_wooden   485.833201
69            Building_type_apartment   432.437679
76   Construction_status_ready_to_use   391.845786
77  Construction_status_to_completion   325.990756
2                 building_floors_num   323.696341
34                          floor_num   315.967698
3                           rooms_num   289.864371
11      Extras_types_air_conditioning   282.383245
52                      district_Wola   265.199542
13               Extras_types_balcony   188.918810
83                      Heating_urban   188.315507
6           Equipment_types_furniture   164.443512
16                Extras_types_garden   162.097546
56            Building_material_brick   158.490793
49                     district_Wawer   153.862225
39                    district_Bemowo   138.977967
67  Building_ownership_full_ownership   128.395893
4          Equipment_types_dishwasher   123.863883
25                  Media_types_phone   121.156862

In [43]:
featureScores.query("Score>40").shape

(51, 2)

In [44]:
top_features=featureScores.nlargest(30,'Score').Specs.unique()

In [45]:
featureScores.sort_values(by="Score",inplace=True,ascending=False)

import plotly.express as px
fig = px.bar(featureScores, x='Specs', y='Score')
fig.show()

In [46]:
X=X[top_features]

## Spliting into train and test sets

In [47]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [48]:
y_train.reset_index(drop=True,inplace=True)
y_test.reset_index(drop=True,inplace=True)

X_train.reset_index(drop=True,inplace=True)
X_test.reset_index(drop=True,inplace=True)

# Training initial model

In [49]:
from sklearn.ensemble import RandomForestRegressor

## Hyper parameters selection

In [50]:
param_grid = [
   
    
    { "bootstrap":[False],
     "n_estimators":[300],
     "max_features":[10,15,20,30],"max_depth":[10,15,20,25,30],"min_samples_leaf":[3,6,12],"min_samples_split":[6,12,24],
     "min_impurity_decrease":[0.01,0.03,0.1,0.3]
},
    
]

In [51]:
from sklearn.model_selection import GridSearchCV

In [52]:
forest_cl=RandomForestRegressor(random_state=10, n_jobs=2)

In [53]:
grid_search = GridSearchCV(forest_cl, param_grid, cv=4,
                          scoring="neg_mean_absolute_error",return_train_score=True)

In [54]:
#grid_search.fit(X_train, y_train)
#rf_clf_best_params = grid_search.best_estimator_


In [55]:
#grid_search.best_params_

In [56]:
#grid_search.best_params_.keys()

In [57]:
#rf_model=grid_search.best_estimator_

rf_model=RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=20, max_features=30, max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.01,
                      min_impurity_split=None, min_samples_leaf=3,
                      min_samples_split=6, min_weight_fraction_leaf=0.0,
                      n_estimators=300, n_jobs=2, oob_score=False,
                      random_state=10, verbose=0, warm_start=False)

In [58]:
rf_model.fit(X_train,y_train)

RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=20, max_features=30, max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.01,
                      min_impurity_split=None, min_samples_leaf=3,
                      min_samples_split=6, min_weight_fraction_leaf=0.0,
                      n_estimators=300, n_jobs=2, oob_score=False,
                      random_state=10, verbose=0, warm_start=False)

In [59]:
rf_model.score(X_train,y_train)

0.8948822323367762

In [60]:
rf_model.score(X_test,y_test)

0.6942192231860257

In [61]:
importance_df=pd.DataFrame(rf_model.feature_importances_,columns=["coefficients"])
importance_df["features"]=X.columns
importance_df.sort_values(by="coefficients",inplace=True)

In [62]:

trace0=go.Bar(
        x=importance_df.coefficients,
        y=importance_df.features,
        orientation="h",
        
        marker=dict(
        color="blue",

        opacity=0.5
        ),
       
    )








data=[trace0]
figure=go.Figure(
    data=data,
    layout=go.Layout(
        title="RF Classifier - Feature importance",
        xaxis=dict(title="Importance"),
        yaxis=dict(title="Feature")

    
    ))
iplot(figure)

In [63]:
def performance_summary(model, X_test, y_test ):
    
    y_hat=model.predict(X_test)
    
    df_summary=pd.DataFrame(y_hat, columns=["y_hat"])
    df_summary["y_true"]=y_test
    df_summary["abs_error"]=np.abs(df_summary.y_true-df_summary.y_hat)
    df_summary["error"]=df_summary.y_hat-df_summary.y_true
    df_summary["relative_error"]= df_summary["error"]/df_summary.y_true
    df_summary["relative_abs_error"]= df_summary["abs_error"]/df_summary.y_true
    
    print("Share of forecasts within 25% absolute error {:.3f}\n".format(df_summary.query("relative_abs_error<0.25").shape[0]/df_summary.shape[0]))
    
    print("Share of forecasts within 10% absolute error {:.3f}\n".format(df_summary.query("relative_abs_error<0.10").shape[0]/df_summary.shape[0]))
    
    print("Share of forecasts within 5% absolute error {:.3f}\n".format(df_summary.query("relative_abs_error<0.05").shape[0]/df_summary.shape[0]))
    
    return(df_summary)
    

## Error analysis

In [64]:
df_summary=performance_summary(rf_model, X_test, y_test)

Share of forecasts within 25% absolute error 0.931

Share of forecasts within 10% absolute error 0.681

Share of forecasts within 5% absolute error 0.445



In [65]:
df_summary.describe()

y_hat        y_true     abs_error         error  relative_error  \
count   2330.000000   2330.000000   2330.000000   2330.000000     2330.000000   
mean   11115.221709  11115.604721   1054.023484     -0.383012        0.018684   
std     2445.812283   2986.134603   1270.907009   1651.256188        0.142342   
min     5948.696700   5357.000000      0.785800 -11647.491826       -0.465900   
25%     9409.605871   9007.750000    250.442715   -572.386772       -0.049092   
50%    10895.196716  10698.000000    651.088525     61.157643        0.006108   
75%    12400.003881  12498.250000   1392.450294    716.763620        0.070896   
max    23270.928575  25000.000000  11647.491826  10065.413455        1.455818   

       relative_abs_error  
count         2330.000000  
mean             0.092704  
std              0.109603  
min              0.000077  
25%              0.023930  
50%              0.057948  
75%              0.122748  
max              1.455818

In [66]:
df_summary.head()

y_hat  y_true    abs_error        error  relative_error  \
0  11549.840741   12105   555.159259  -555.159259       -0.045862   
1  12692.447437   12831   138.552563  -138.552563       -0.010798   
2  10393.201605    9224  1169.201605  1169.201605        0.126756   
3   9206.581258    9346   139.418742  -139.418742       -0.014917   
4  11905.078672   11906     0.921328    -0.921328       -0.000077   

   relative_abs_error  
0            0.045862  
1            0.010798  
2            0.126756  
3            0.014917  
4            0.000077

In [67]:


trace0=go.Scatter(
        name="Predicted",
        y=df_summary.y_true,
        x=df_summary.y_true,
        mode='lines',
        marker=dict(
        size=5,
        opacity=0.3
        ),
       
    )




trace1=go.Scatter(
        name="Actual",
        y=df_summary.y_hat,
        x=df_summary.y_true,
        mode='markers',
        marker=dict(
        color="blue",
    
        size=5,
        opacity=0.1
        ),
        text=df_summary.error
       
    )




data=[trace0,trace1]
figure=go.Figure(
    data=data,
    layout=go.Layout(
        title="Predicted vs actual unit price",
        yaxis=dict(title="Predicted price",range=(0,25000)),
        xaxis=dict(title="Actual price")

    
    ))

iplot(figure)

In [68]:
counts, bins = np.histogram(df_summary.relative_error*100,bins=range(-50,50,2))
counts=counts/df_summary.shape[0]*100
bins=bins[1:]

In [69]:

fig = px.bar(x=bins, y=counts, labels={"x":"relative variance [%]", "y":"count"})
fig.show()

# Neural networks models

## Transforming and scaling data for NN

In [70]:
def DNN_plot_loss(history, starting_epoch):

        trace0=go.Scatter(
                y=history.history['loss'][starting_epoch:],
                x=history.epoch[starting_epoch:],
                mode='lines',
                marker=dict(
                color="blue",
                size=5,
                opacity=0.5
                ),
                name="Training Loss"
            )


        trace1=go.Scatter(
                y=history.history['val_loss'][starting_epoch:],
                x=history.epoch[starting_epoch:],
                mode='lines',
                marker=dict(
                color="red",
                size=5,
                opacity=0.5
                ),
                name="Validation Loss"
            )

        data=[trace0, trace1]
        figure=go.Figure(
            data=data,
            layout=go.Layout(
                title="Learning curve",
                yaxis=dict(title="Loss"),
                xaxis=dict(title="Epoch",range=(starting_epoch,history.epoch[-1])),
                legend=dict(
                    x=1,
                    y=1,
                    traceorder="normal",
                    font=dict(
                        family="sans-serif",
                        size=12,
                        color="black"
                    ),
                bgcolor=None


            )))
        iplot(figure)

In [71]:
y_train=np.asarray(y_train).reshape(-1,1)
y_train.shape

(9317, 1)

In [72]:
y_test=np.asarray(y_test).reshape(-1,1)
y_test.shape

(2330, 1)

In [73]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()

In [74]:
X_train=scaler.fit_transform(X_train)
X_test=scaler.transform(X_test)

In [75]:
X_train.shape

(9317, 30)

In [76]:
X_test.shape

(2330, 30)

## Initial model

In [77]:
tf.keras.backend.clear_session()
tf.random.set_seed(60)

DNN=keras.models.Sequential([
    
    keras.layers.Dense(1024, input_dim = X_train.shape[1]),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.4),
    keras.layers.BatchNormalization(),

    keras.layers.Dense(units=512),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.3),
    keras.layers.BatchNormalization(),
    
    keras.layers.Dense(units=512),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.2),
    keras.layers.BatchNormalization(),
    
    keras.layers.Dense(units=256),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.2),
    keras.layers.BatchNormalization(),
    
    keras.layers.Dense(units=256),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.1),
    keras.layers.BatchNormalization(),
    
    keras.layers.Dense(units=128),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.05),
    keras.layers.Dense(units=1, activation="linear"),



])

In [78]:
DNN.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 1024)              31744     
_________________________________________________________________
leaky_re_lu (LeakyReLU)      (None, 1024)              0         
_________________________________________________________________
dropout (Dropout)            (None, 1024)              0         
_________________________________________________________________
batch_normalization (BatchNo (None, 1024)              4096      
_________________________________________________________________
dense_1 (Dense)              (None, 512)               524800    
_________________________________________________________________
leaky_re_lu_1 (LeakyReLU)    (None, 512)               0         
_________________________________________________________________
dropout_1 (Dropout)          (None, 512)               0

In [79]:
checkpoint_name = 'Weights-{epoch:03d}--{val_loss:.5f}.hdf5' 
checkpoint = ModelCheckpoint(checkpoint_name, monitor='val_loss', verbose = 1, save_best_only = True, mode ='auto')
callbacks_list = [checkpoint]

In [80]:
t1=datetime.now()

In [81]:
optimizer = keras.optimizers.Adam(lr=0.01, decay=8e-5)



DNN.compile(optimizer=optimizer, 
            loss='mean_absolute_error',
            metrics=['mean_absolute_error'])


history = DNN.fit(X_train, y_train,
                    epochs=300,batch_size=512,
                    validation_data=(X_test, y_test),
                    callbacks=callbacks_list,
                    verbose=1)

Train on 9317 samples, validate on 2330 samples
Epoch 1/300
7680/9317 [=======================>......] - ETA: 0s - loss: 11076.6660 - mean_absolute_error: 11076.6670
Epoch 00001: val_loss improved from inf to 6774.90706, saving model to Weights-001--6774.90706.hdf5
9317/9317 [==============================] - 3s 319us/sample - loss: 11042.0993 - mean_absolute_error: 11042.0996 - val_loss: 6774.9071 - val_mean_absolute_error: 6774.9067
Epoch 2/300
7680/9317 [=======================>......] - ETA: 0s - loss: 10404.1997 - mean_absolute_error: 10404.2012
Epoch 00002: val_loss improved from 6774.90706 to 5136.79004, saving model to Weights-002--5136.79004.hdf5
9317/9317 [==============================] - 0s 43us/sample - loss: 10274.7057 - mean_absolute_error: 10274.7070 - val_loss: 5136.7900 - val_mean_absolute_error: 5136.7900
Epoch 3/300
8192/9317 [=========================>....] - ETA: 0s - loss: 7707.4402 - mean_absolute_error: 7707.4409
Epoch 00003: val_loss did not improve from 5136.

8704/9317 [===========================>..] - ETA: 0s - loss: 1330.7614 - mean_absolute_error: 1330.7615
Epoch 00023: val_loss did not improve from 1361.56763
9317/9317 [==============================] - 0s 26us/sample - loss: 1332.1993 - mean_absolute_error: 1332.1993 - val_loss: 1449.6121 - val_mean_absolute_error: 1449.6122
Epoch 24/300
7168/9317 [======================>.......] - ETA: 0s - loss: 1339.9934 - mean_absolute_error: 1339.9933
Epoch 00024: val_loss improved from 1361.56763 to 1342.10056, saving model to Weights-024--1342.10056.hdf5
9317/9317 [==============================] - 0s 37us/sample - loss: 1335.3522 - mean_absolute_error: 1335.3522 - val_loss: 1342.1006 - val_mean_absolute_error: 1342.1006
Epoch 25/300
8192/9317 [=========================>....] - ETA: 0s - loss: 1331.5861 - mean_absolute_error: 1331.5861
Epoch 00025: val_loss did not improve from 1342.10056
9317/9317 [==============================] - 0s 27us/sample - loss: 1335.6880 - mean_absolute_error: 1335.6

Epoch 46/300
8192/9317 [=========================>....] - ETA: 0s - loss: 1271.4924 - mean_absolute_error: 1271.4924
Epoch 00046: val_loss improved from 1256.12451 to 1242.94881, saving model to Weights-046--1242.94881.hdf5
9317/9317 [==============================] - 0s 36us/sample - loss: 1274.0771 - mean_absolute_error: 1274.0771 - val_loss: 1242.9488 - val_mean_absolute_error: 1242.9487
Epoch 47/300
8192/9317 [=========================>....] - ETA: 0s - loss: 1249.4040 - mean_absolute_error: 1249.4041
Epoch 00047: val_loss did not improve from 1242.94881
9317/9317 [==============================] - 0s 25us/sample - loss: 1249.0572 - mean_absolute_error: 1249.0573 - val_loss: 1264.9788 - val_mean_absolute_error: 1264.9788
Epoch 48/300
6656/9317 [====================>.........] - ETA: 0s - loss: 1242.5508 - mean_absolute_error: 1242.5508
Epoch 00048: val_loss did not improve from 1242.94881
9317/9317 [==============================] - 0s 28us/sample - loss: 1255.6205 - mean_absolute_

8704/9317 [===========================>..] - ETA: 0s - loss: 1210.5597 - mean_absolute_error: 1210.5596
Epoch 00069: val_loss did not improve from 1219.60044
9317/9317 [==============================] - 0s 28us/sample - loss: 1211.2329 - mean_absolute_error: 1211.2328 - val_loss: 1245.2112 - val_mean_absolute_error: 1245.2112
Epoch 70/300
9216/9317 [============================>.] - ETA: 0s - loss: 1222.2011 - mean_absolute_error: 1222.2009
Epoch 00070: val_loss did not improve from 1219.60044
9317/9317 [==============================] - 0s 29us/sample - loss: 1223.3311 - mean_absolute_error: 1223.3311 - val_loss: 1223.8756 - val_mean_absolute_error: 1223.8756
Epoch 71/300
8192/9317 [=========================>....] - ETA: 0s - loss: 1218.7272 - mean_absolute_error: 1218.7273
Epoch 00071: val_loss did not improve from 1219.60044
9317/9317 [==============================] - 0s 25us/sample - loss: 1217.7938 - mean_absolute_error: 1217.7938 - val_loss: 1244.3968 - val_mean_absolute_error: 

Epoch 93/300
9216/9317 [============================>.] - ETA: 0s - loss: 1185.6433 - mean_absolute_error: 1185.6432
Epoch 00093: val_loss did not improve from 1204.98430
9317/9317 [==============================] - 0s 26us/sample - loss: 1188.1108 - mean_absolute_error: 1188.1107 - val_loss: 1205.7554 - val_mean_absolute_error: 1205.7555
Epoch 94/300
8192/9317 [=========================>....] - ETA: 0s - loss: 1191.1338 - mean_absolute_error: 1191.1338
Epoch 00094: val_loss did not improve from 1204.98430
9317/9317 [==============================] - 0s 25us/sample - loss: 1198.9489 - mean_absolute_error: 1198.9489 - val_loss: 1253.8710 - val_mean_absolute_error: 1253.8710
Epoch 95/300
8192/9317 [=========================>....] - ETA: 0s - loss: 1175.6158 - mean_absolute_error: 1175.6158
Epoch 00095: val_loss did not improve from 1204.98430
9317/9317 [==============================] - 0s 24us/sample - loss: 1171.5448 - mean_absolute_error: 1171.5449 - val_loss: 1211.5686 - val_mean_abs

...

Epoch 189/300
8192/9317 [=========================>....] - ETA: 0s - loss: 1092.9051 - mean_absolute_error: 1092.9052
Epoch 00189: val_loss did not improve from 1173.20881
9317/9317 [==============================] - 0s 27us/sample - loss: 1091.6634 - mean_absolute_error: 1091.6635 - val_loss: 1200.5610 - val_mean_absolute_error: 1200.5609
Epoch 190/300
8704/9317 [===========================>..] - ETA: 0s - loss: 1092.9350 - mean_absolute_error: 1092.9349
Epoch 00190: val_loss did not improve from 1173.20881
9317/9317 [==============================] - 0s 24us/sample - loss: 1091.4404 - mean_absolute_error: 1091.4404 - val_loss: 1200.1490 - val_mean_absolute_error: 1200.1490
Epoch 191/300
9216/9317 [============================>.] - ETA: 0s - loss: 1101.2073 - mean_absolute_error: 1101.2073
Epoch 00191: val_loss did not improve from 1173.20881
9317/9317 [==============================] - 0s 26us/sample - loss: 1099.9864 - mean_absolute_error: 1099.9863 - val_loss: 1191.4883 - val_mean_

Epoch 213/300
7680/9317 [=======================>......] - ETA: 0s - loss: 1095.8542 - mean_absolute_error: 1095.8541
Epoch 00213: val_loss did not improve from 1167.23403
9317/9317 [==============================] - 0s 28us/sample - loss: 1099.4205 - mean_absolute_error: 1099.4204 - val_loss: 1217.1484 - val_mean_absolute_error: 1217.1484
Epoch 214/300
7680/9317 [=======================>......] - ETA: 0s - loss: 1094.8502 - mean_absolute_error: 1094.8502
Epoch 00214: val_loss did not improve from 1167.23403
9317/9317 [==============================] - 0s 27us/sample - loss: 1095.8023 - mean_absolute_error: 1095.8022 - val_loss: 1194.6178 - val_mean_absolute_error: 1194.6177
Epoch 215/300
8704/9317 [===========================>..] - ETA: 0s - loss: 1077.5451 - mean_absolute_error: 1077.5452
Epoch 00215: val_loss improved from 1167.23403 to 1166.01595, saving model to Weights-215--1166.01595.hdf5
9317/9317 [==============================] - 0s 42us/sample - loss: 1085.0158 - mean_absolu

Epoch 237/300
8192/9317 [=========================>....] - ETA: 0s - loss: 1051.6321 - mean_absolute_error: 1051.6322
Epoch 00237: val_loss did not improve from 1166.01595
9317/9317 [==============================] - 0s 25us/sample - loss: 1052.7340 - mean_absolute_error: 1052.7340 - val_loss: 1181.7180 - val_mean_absolute_error: 1181.7180
Epoch 238/300
8192/9317 [=========================>....] - ETA: 0s - loss: 1048.7379 - mean_absolute_error: 1048.7379
Epoch 00238: val_loss did not improve from 1166.01595
9317/9317 [==============================] - 0s 24us/sample - loss: 1049.9034 - mean_absolute_error: 1049.9033 - val_loss: 1193.1435 - val_mean_absolute_error: 1193.1434
Epoch 239/300
9216/9317 [============================>.] - ETA: 0s - loss: 1043.7475 - mean_absolute_error: 1043.7476
Epoch 00239: val_loss did not improve from 1166.01595
9317/9317 [==============================] - 0s 25us/sample - loss: 1043.9473 - mean_absolute_error: 1043.9473 - val_loss: 1194.1492 - val_mean_

Epoch 261/300
8704/9317 [===========================>..] - ETA: 0s - loss: 1036.2576 - mean_absolute_error: 1036.2577
Epoch 00261: val_loss did not improve from 1163.87742
9317/9317 [==============================] - 0s 26us/sample - loss: 1039.2624 - mean_absolute_error: 1039.2625 - val_loss: 1178.2324 - val_mean_absolute_error: 1178.2324
Epoch 262/300
8704/9317 [===========================>..] - ETA: 0s - loss: 1051.2277 - mean_absolute_error: 1051.2277
Epoch 00262: val_loss did not improve from 1163.87742
9317/9317 [==============================] - 0s 26us/sample - loss: 1055.2485 - mean_absolute_error: 1055.2484 - val_loss: 1190.3171 - val_mean_absolute_error: 1190.3171
Epoch 263/300
6656/9317 [====================>.........] - ETA: 0s - loss: 1072.6226 - mean_absolute_error: 1072.6227
Epoch 00263: val_loss did not improve from 1163.87742
9317/9317 [==============================] - 0s 25us/sample - loss: 1064.7614 - mean_absolute_error: 1064.7614 - val_loss: 1207.2616 - val_mean_

Epoch 285/300
8704/9317 [===========================>..] - ETA: 0s - loss: 1034.9465 - mean_absolute_error: 1034.9465
Epoch 00285: val_loss did not improve from 1163.87742
9317/9317 [==============================] - 0s 25us/sample - loss: 1035.7823 - mean_absolute_error: 1035.7823 - val_loss: 1173.8761 - val_mean_absolute_error: 1173.8762
Epoch 286/300
9216/9317 [============================>.] - ETA: 0s - loss: 1032.3078 - mean_absolute_error: 1032.3079
Epoch 00286: val_loss did not improve from 1163.87742
9317/9317 [==============================] - 0s 24us/sample - loss: 1033.6468 - mean_absolute_error: 1033.6469 - val_loss: 1167.5449 - val_mean_absolute_error: 1167.5448
Epoch 287/300
8704/9317 [===========================>..] - ETA: 0s - loss: 1041.4159 - mean_absolute_error: 1041.4158
Epoch 00287: val_loss did not improve from 1163.87742
9317/9317 [==============================] - 0s 25us/sample - loss: 1041.1709 - mean_absolute_error: 1041.1709 - val_loss: 1175.9278 - val_mean_

In [82]:
weights_file = 'Weights-236--1166.82550.hdf5' # choose the best checkpoint 
DNN.load_weights(weights_file) # load it
DNN.compile(loss='mean_absolute_error', optimizer='adam', metrics=['mean_absolute_error'])

In [83]:
t2=datetime.now()

In [84]:
(t2-t1).seconds

79

In [85]:
DNN_plot_loss(history,starting_epoch=10)

In [92]:
df_summary_dnn=performance_summary(DNN,X_test, y_test)
#d

Share of forecasts within 25% absolute error 0.926

Share of forecasts within 10% absolute error 0.638

Share of forecasts within 5% absolute error 0.381



In [93]:
df_summary_dnn.describe()

y_hat        y_true     abs_error         error  relative_error  \
count   2330.000000   2330.000000   2330.000000   2330.000000     2330.000000   
mean   10909.083008  11115.604721   1166.825485   -206.516382        0.001588   
std     2373.523438   2986.134603   1353.992657   1775.583025        0.142053   
min     6166.135742   5357.000000      0.512207 -13585.668945       -0.550500   
25%     9245.732666   9007.750000    305.752930   -844.804688       -0.074616   
50%    10662.800781  10698.000000    738.214844    -45.675293       -0.004523   
75%    12067.731934  12498.250000   1517.845215    638.089600        0.065042   
max    22237.052734  25000.000000  13585.668945   8470.246094        0.929840   

       relative_abs_error  
count         2330.000000  
mean             0.099999  
std              0.100883  
min              0.000067  
25%              0.029890  
50%              0.069934  
75%              0.137207  
max              0.929840

In [94]:
def plot_predictions(df_summary):

    trace0=go.Scatter(
            name="Predicted",
            y=df_summary.y_true,
            x=df_summary.y_true,
            mode='lines',
            marker=dict(
            size=5,
            opacity=0.3
            ),

        )




    trace1=go.Scatter(
            name="Actual",
            y=df_summary.y_hat,
            x=df_summary.y_true,
            mode='markers',
            marker=dict(
            color="blue",

            size=5,
            opacity=0.1
            ),
            text=df_summary_dnn.error

        )




    data=[trace0,trace1]
    figure=go.Figure(
        data=data,
        layout=go.Layout(
            title="Predicted vs actual unit price",
            yaxis=dict(title="Predicted price",range=(0,25000)),
            xaxis=dict(title="Actual price")


        ))

    iplot(figure)

In [95]:
plot_predictions(df_summary_dnn)

## Modified model

In [90]:
tf.keras.backend.clear_session()
tf.random.set_seed(60)


DNN_mod=keras.models.Sequential([
    
    keras.layers.Dense(1034, input_dim = X_train.shape[1]),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.5),
    keras.layers.BatchNormalization(),
    
    keras.layers.Dense(units=512),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.2),
    keras.layers.BatchNormalization(),
    
    keras.layers.Dense(units=256),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.2),
    keras.layers.BatchNormalization(),
    
    keras.layers.Dense(units=256),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.1),
    keras.layers.BatchNormalization(),
    
    keras.layers.Dense(units=128),
    keras.layers.LeakyReLU(),
    keras.layers.Dropout(0.1),
    keras.layers.Dense(units=1, activation="linear"),



])

In [91]:
t1=datetime.now()
optimizer = keras.optimizers.Adam(lr=0.01, decay=8e-5)




DNN_mod.compile(optimizer=optimizer, 
            loss='mean_absolute_error',
            metrics=['mean_absolute_error'])


history2 = DNN_mod.fit(X_train, y_train,
                    epochs=300,batch_size=512,
                    validation_data=(X_test, y_test),
                    verbose=1)

Train on 9317 samples, validate on 2330 samples
Epoch 1/300
9317/9317 [==============================] - 2s 220us/sample - loss: 11058.8794 - mean_absolute_error: 11058.8789 - val_loss: 9112.7404 - val_mean_absolute_error: 9112.7412
Epoch 2/300
9317/9317 [==============================] - 0s 21us/sample - loss: 10377.8496 - mean_absolute_error: 10377.8506 - val_loss: 5377.4516 - val_mean_absolute_error: 5377.4521
Epoch 3/300
9317/9317 [==============================] - 0s 21us/sample - loss: 7658.1601 - mean_absolute_error: 7658.1602 - val_loss: 10879.8748 - val_mean_absolute_error: 10879.8750
Epoch 4/300
9317/9317 [==============================] - 0s 21us/sample - loss: 2766.1751 - mean_absolute_error: 2766.1753 - val_loss: 50896.1320 - val_mean_absolute_error: 50896.1328
Epoch 5/300
9317/9317 [==============================] - 0s 22us/sample - loss: 1739.3895 - mean_absolute_error: 1739.3896 - val_loss: 26624.6168 - val_mean_absolute_error: 26624.6152
Epoch 6/300
9317/9317 [========

KeyboardInterrupt: 

In [ ]:
t2=datetime.now()
(t2-t1).seconds

In [ ]:
DNN_plot_loss(history2,starting_epoch=10)

In [ ]:
df_summary_dnn_mod=performance_summary(DNN_mod, X_test, y_test)
#df_summary_dnn_mod=performance_summary(DNN_mod, X_train, y_train)

In [ ]:
df_summary_dnn_mod.describe()

In [ ]:
plot_predictions(df_summary_dnn_mod)